In [20]:
from PIL import Image
import numpy as np
import os
# Cut image to 64*64

def cut_image(path, cut_path, size):
    '''
    剪切图片
    :param path: 输入图片路径
    :param cut_path: 剪切图片后的输出路径
    :param size: 要剪切的图片大小
    :return:
    '''
    for (root, dirs, files) in os.walk(path):
        temp = root.replace(path, cut_path)
        if not os.path.exists(temp):
            os.makedirs(temp)
        for file in files:

            print(file)
            image, flag = cut(Image.open(os.path.join(root, file)))
            if not flag: Image.fromarray(image).convert('L').resize((size, size)).save(os.path.join(temp, file))
        #print(temp)
    pass

def cut(image):
    '''
    通过找到人的最小最大高度与宽度把人的轮廓分割出来，、
    因为原始轮廓图为二值图，因此头顶为将二值图像列相加后，形成一列后第一个像素值不为0的索引。
    同理脚底为形成一列后最后一个像素值不为0的索引。
    人的宽度也同理。
    :param image: 需要裁剪的图片 N*M的矩阵
    :return: temp:裁剪后的图片 size*size的矩阵。flag：是否是符合要求的图片
    '''
    # 找到人的最小最大高度与宽度
    height_min = (image.sum(axis=1) != 0).argmax()
    height_max = ((image.sum(axis=1) != 0).cumsum()).argmax()
    width_min = (image.sum(axis=0) != 0).argmax()
    width_max = ((image.sum(axis=0) != 0).cumsum()).argmax()
    head_top = image[height_min, :].argmax()
    # 设置切割后图片的大小，为size*size，因为人的高一般都会大于宽
    size = height_max - height_min
    temp = np.zeros((size, size))
    # 将width_max-width_min（宽）乘height_max-height_min（高，szie）的人的轮廓图，放在size*size的图片中央
    # l = (width_max-width_min)//2
    # r = width_max-width_min-l
    # 以头为中心，将将width_max-width_min（宽）乘height_max-height_min（高，szie）的人的轮廓图，放在size*size的图片中央
    l1 = head_top - width_min
    r1 = width_max - head_top
    # 若宽大于高，或头的左侧或右侧身子比要生成图片的一般要大。则此图片为不符合要求的图片
    flag = False
    if size <= width_max - width_min or size // 2 < r1 or size // 2 < l1:
        flag = True
        return temp, flag
    # centroid = np.array([(width_max+width_min)/2,(height_max+height_min)/2],dtype='int')
    temp[:, (size // 2 - l1):(size // 2 + r1)] = image[height_min:height_max, width_min:width_max]
    return temp, flag

In [20]:
from PIL import Image
import os

def convert_to_black_and_white(input_path, output_path):
    # 打开图片
    img = Image.open(input_path)

    # 获取图片的宽和高
    width, height = img.size

    # 遍历每个像素
    for x in range(width):
        for y in range(height):
            # 获取像素的RGB值
            r, g, b = img.getpixel((x, y))

            # 如果不是黑色，则设置为白色
            if r >=30 and g >=30  and b >= 30:
                img.putpixel((x, y), (255, 255, 255))
            else:
                img.putpixel((x, y), (0, 0, 0))

    # 保存处理后的图片
    img.save(output_path)

def process_images_in_folder(folder_path):
    # 确保文件夹路径以斜杠结尾
    folder_path = os.path.join(folder_path, "")

    # 遍历文件夹中的所有图片文件
    for file_name in os.listdir(folder_path):
        if file_name.endswith((".jpg")):
            input_path = os.path.join(folder_path, file_name)
            output_path = input_path
            convert_to_black_and_white(input_path, output_path)

# 示例：传入文件夹路径，处理其中所有图片
# input_folder_path = r"D:\unity project\My project\dataset\mxh-221_1\216"
# process_images_in_folder(input_folder_path,input_folder_path)


In [10]:
from PIL import Image
# Resize Image as person for 64
def resize_and_center_image(input_path, target_size):
    # 打开原始图像
    original_image = Image.open(input_path)

    # 缩小图像
    original_image.thumbnail((original_image.width / 4, original_image.height / 3.75))

    # 获取原始图像的尺寸
    original_size = original_image.size

    # 计算扩充后图像的左上角坐标
    left = (target_size[0] - original_size[0]) // 2
    top = (target_size[1] - original_size[1]) // 2

    # 创建一个空白的目标图像
    target_image = Image.new("RGB", target_size, color="black")

    # 将缩小后的图像粘贴到目标图像的中心
    target_image.paste(original_image, (left, top))

    # 构造输出路径，保存到原始图像的路径
    output_path = input_path

    # 保存扩充后的图像
    target_image.save(output_path)



In [3]:
import os
from PIL import Image
to_delete=[]
def process_images_in_subsubsubfolders(folder_path, target_size, depth=3):
    # 递归函数，遍历文件夹及其子文件夹，直到指定深度
    def recursive_process(current_path, current_depth):
        if current_depth <= depth:
            for item in os.listdir(current_path):
                item_path = os.path.join(current_path, item)
                if os.path.isdir(item_path):
                    recursive_process(item_path, current_depth + 1)
                elif item.lower().endswith(('.jpg')):
                    #print(item_path)
                    #resize_and_center_image(item_path, target_size)
                    with Image.open(item_path) as img:
                        if(img.size!=(64,64)):
                            #print(item_path)
                            to_delete.append(item_path)
                            #os.remove(item_path)
                        #if img.size == target_size:

    recursive_process(folder_path, 0)

folder_path = r'D:\dataset\clean_data'
target_size = (320, 240)
process_images_in_subsubsubfolders(folder_path, target_size)
print(to_delete)

['D:\\dataset\\clean_data\\02\\072\\216\\0000.jpg', 'D:\\dataset\\clean_data\\02\\072\\288\\0199.jpg', 'D:\\dataset\\clean_data\\02\\072\\72\\0181.jpg', 'D:\\dataset\\clean_data\\02\\086\\0\\0000.jpg', 'D:\\dataset\\clean_data\\02\\086\\144\\0015.jpg', 'D:\\dataset\\clean_data\\02\\086\\144\\0060.jpg', 'D:\\dataset\\clean_data\\02\\086\\144\\0061.jpg', 'D:\\dataset\\clean_data\\02\\086\\144\\0130.jpg', 'D:\\dataset\\clean_data\\02\\086\\144\\0131.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0076.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0151.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0152.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0153.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0190.jpg', 'D:\\dataset\\clean_data\\02\\086\\216\\0191.jpg', 'D:\\dataset\\clean_data\\02\\086\\288\\0003.jpg', 'D:\\dataset\\clean_data\\02\\086\\288\\0004.jpg', 'D:\\dataset\\clean_data\\02\\086\\288\\0005.jpg', 'D:\\dataset\\clean_data\\02\\086\\288\\0007.jpg', 'D:\\dataset\\clean_data\\02\\086

In [8]:
for i in to_delete:
    os.remove(i)

In [18]:
import os

def process_images_in_subsubsubfolders(folder_path, target_size, depth=3, skip_dirs=('013', '017', '034')):
    # 递归函数，遍历文件夹及其子文件夹，直到指定深度
    def recursive_process(current_path, current_depth):
        nonlocal flag  # 使用nonlocal关键字引用外部变量
        if current_depth <= depth:
            for item in os.listdir(current_path):
                item_path = os.path.join(current_path, item)
                if os.path.isdir(item_path):
                    # 检查当前文件夹名称是否在要跳过的目录列表中
                    if os.path.basename(item_path) not in skip_dirs:
                        recursive_process(item_path, current_depth + 1)
                elif item.lower().endswith(('.jpg')):
                    
                    if flag:  # 如果标志为真，则执行 resize_and_center_image
                        resize_and_center_image(item_path, target_size)
                    else:
                        flag = (item_path == r'D:\dataset\clean_data\02\175\288\0097.jpg')  # 设置标志为真的条件

    flag = False
    recursive_process(folder_path, 0)

folder_path = r'D:\dataset\clean_data'
target_size = (320, 240)
process_images_in_subsubsubfolders(folder_path, target_size)


In [34]:
#D:\dataset\test_1
def preatment(folder_path):
    for file_name in os.listdir(folder_path):
        input_path=os.path.join(folder_path,file_name)
        output_path=input_path
        #convert_to_black_and_white(input_path,input_path)
        image=Image.open(input_path)
        image_array = np.array(image)
        binary_array = image_array[:, :, 0]
        image, flag =cut(binary_array)
        if not flag: Image.fromarray(image).convert('L').resize((64, 64)).save(output_path)

preatment(r'D:\dataset\test_1')

        

In [30]:
import os

def traverse_third_level_folders(folder_path):
    for root, dirs, files in os.walk(folder_path):
        for dir_name in dirs:
            subfolder_path = os.path.join(root, dir_name)
            subsubfolders = [subsubfolder for subsubfolder in os.listdir(subfolder_path)
                             if os.path.isdir(os.path.join(subfolder_path, subsubfolder))]
            for subsubfolder in subsubfolders:
                subsubfolder_path = os.path.join(subfolder_path, subsubfolder)
                third_level_folders = [third_level_folder for third_level_folder in os.listdir(subsubfolder_path)
                                       if os.path.isdir(os.path.join(subsubfolder_path, third_level_folder))]
                for third_level_folder in third_level_folders:
                    third_level_folder_path = os.path.join(subsubfolder_path, third_level_folder)
                    preatment(third_level_folder_path)

# 例子
folder_path = r'D:\dataset\clean_data'
traverse_third_level_folders(folder_path)


In [2]:
import os
import shutil

def delete_subfolder_with_name(root_path, target_folder_name):
    for root, dirs, files in os.walk(root_path):
        for dir_name in dirs:
            parent_folder_path = os.path.join(root, dir_name)
            target_folder_path = os.path.join(parent_folder_path, target_folder_name)
            
            # 检查目标文件夹是否存在
            if os.path.exists(target_folder_path):
                shutil.rmtree(target_folder_path)
                print(f"Deleted folder: {target_folder_path}")

# 示例用法
root_directory = r"D:\dataset\clean_data"
target_folder_name = "017"

delete_subfolder_with_name(root_directory, target_folder_name)


Deleted folder: D:\dataset\clean_data\02\017
Deleted folder: D:\dataset\clean_data\05\017
Deleted folder: D:\dataset\clean_data\06\017
Deleted folder: D:\dataset\clean_data\07\017
Deleted folder: D:\dataset\clean_data\08\017
Deleted folder: D:\dataset\clean_data\10\017
Deleted folder: D:\dataset\clean_data\12\017
Deleted folder: D:\dataset\clean_data\15\017
Deleted folder: D:\dataset\clean_data\16\017
Deleted folder: D:\dataset\clean_data\17\017
Deleted folder: D:\dataset\clean_data\26\017
Deleted folder: D:\dataset\clean_data\27\017
Deleted folder: D:\dataset\clean_data\29\017
Deleted folder: D:\dataset\clean_data\32\017
Deleted folder: D:\dataset\clean_data\35\017
Deleted folder: D:\dataset\clean_data\37\017
Deleted folder: D:\dataset\clean_data\38\017
Deleted folder: D:\dataset\clean_data\39\017
Deleted folder: D:\dataset\clean_data\43\017
Deleted folder: D:\dataset\clean_data\45\017
Deleted folder: D:\dataset\clean_data\46\017
Deleted folder: D:\dataset\clean_data\49\017
Deleted fo